In [1]:
import tensorflow as tf
import os

/Users/manishashivshette/anaconda3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:523: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/Users/manishashivshette/anaconda3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:524: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/Users/manishashivshette/anaconda3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:525: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/Users/manishashivshette/anaconda3/lib/python3

In [2]:
deepfashion_dataset_path = "/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/"

In [3]:
target_attribute_model_folder = "/Users/manishashivshette/Documents/ManishaStudies/CMPE295B/AttributeModel/"

In [4]:
target_attribute_id = 1 # Refer to below deep_attr dictionary to train different attr models

In [5]:
num_epochs = 100
num_steps = 15

In [6]:
deep_attr={1:"texture",2:"fabric",3:"shape",4:"part",5:"style"}

In [7]:
saved_model_path = deepfashion_dataset_path+"models/model-"+deep_attr[target_attribute_id]+".h5"

In [8]:
# Load the attributes names into memory.
with tf.gfile.FastGFile(os.path.join(deepfashion_dataset_path, "Anno/list_attr_cloth.txt"), "r") as f:
    attribute_name_lines = f.readlines()

# Process attribute names.
num_attrs = int(attribute_name_lines.pop(0).strip())
header_attr = attribute_name_lines.pop(0).split()
assert len(attribute_name_lines) == num_attrs, "Wrong number of attributes."
attribute_names = list(map((lambda s: s.lower().split()[0:-1]), attribute_name_lines))

Instructions for updating:
Use tf.gfile.GFile.


In [9]:
import collections
images_hashmap=collections.defaultdict()
# Load the attribute labels into memory.
with tf.gfile.FastGFile(os.path.join(deepfashion_dataset_path, "Anno/list_attr_img.txt"), "r") as f:
    attribute_lines = f.readlines()

# Check images are all loaded.
num_images = int(attribute_lines.pop(0).strip())
header_attr = attribute_lines.pop(0).split()
assert len(attribute_lines) == num_images, "Wrong number of images."

# Assign attribute labels to existing image metadata.
for element in attribute_lines:
    columns = element.split()
    filename = columns[0]
    attributes = []
    for x, v in enumerate(columns[1:]):
        if int(v) == 1:
            attributes.extend(attribute_names[int(x)])
    attribute_ids = [a.strip().lower() for a in attributes]
    
    attribute_ids = [x for x in attribute_ids]
    
    images_hashmap[filename] = attribute_ids
print(images_hashmap)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [10]:
import shutil
import os
import re
import cv2
import splitter
import pandas as pd
import collections

In [11]:
import numpy as np
from six.moves import range

In [12]:
splitter = re.compile("\s+")
base_path = deepfashion_dataset_path + 'img'

In [13]:
attr_file = target_attribute_model_folder+ "list_attr_clothes.csv"

In [14]:
df = pd.read_csv(attr_file)
df.head()    

attribute_name    attribute_type
0        a-line                         3
1        abstract                       1
2        abstract chevron               1
3  abstract chevron print               1
4        abstract diamond               1

In [15]:
#extract expected attributes
df_filted_attribute = df[df['attribute_type']==target_attribute_id]

In [16]:
df_filted_attribute.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 156 entries, 1 to 992
Data columns (total 2 columns):
attribute_name      156 non-null object
attribute_type      156 non-null int64
dtypes: int64(1), object(1)
memory usage: 3.7+ KB


In [17]:
df_filted_attribute['attribute_name  ']=df_filted_attribute['attribute_name  '].str.strip()

/Users/manishashivshette/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [18]:
attribute_dict = dict(zip(df_filted_attribute['attribute_name  '], df_filted_attribute.attribute_type))

In [19]:
def process_folders():
    # Read the relevant annotation file and preprocess it
    # Assumed that the annotation files are under '<project folder>/data/anno' path
    partitition_file_path = deepfashion_dataset_path+"/Eval/list_eval_partition.txt"
    with open(partitition_file_path, 'r') as eval_partition_file:
        list_eval_partition = [line.rstrip('\n') for line in eval_partition_file][2:]
        list_eval_partition = [splitter.split(line) for line in list_eval_partition]
        list_all =[]
        for v in list_eval_partition:
            img_key = v[0][4:]
            img_key= "img/"+img_key
            if img_key in images_hashmap:
                for each_attr in images_hashmap[img_key]:
                    if each_attr in attribute_dict:
                        list_all.append((v[0][4:],each_attr , v[1]))
    print(list_all[0:5])
    count =0
    for element in list_all:
        if not os.path.exists(os.path.join(base_path, element[2])):
            os.mkdir(os.path.join(base_path, element[2]))
        if not os.path.exists(os.path.join(os.path.join(base_path, element[2]), element[1])):
            os.mkdir(os.path.join(os.path.join(base_path, element[2]), element[1]))
        if not os.path.exists(os.path.join(os.path.join(os.path.join(os.path.join(base_path, element[2]), element[1])),
                              element[0].split('/')[0])):
            print(os.path.join(os.path.join(os.path.join(os.path.join(base_path, element[2]), element[1])),
                     element[0].split('/')[0]))
            os.mkdir(os.path.join(os.path.join(os.path.join(os.path.join(base_path, element[2]), element[1])),
                     element[0].split('/')[0]))
        try:
            
            shutil.copyfile(os.path.join(base_path, element[0]),
                os.path.join(os.path.join(os.path.join(base_path, element[2]), element[1]), element[0]))
        except:
            count+=1
            #print(os.path.join(base_path, element[0]))
            #print("one file not found")
    print("file not found count:",count) 

In [20]:
process_folders()

[('Sheer_Pleated-Front_Blouse/img_00000009.jpg', 'sophisticated', 'train'), ('Sheer_Pleated-Front_Blouse/img_00000016.jpg', 'print', 'train'), ('Sheer_Pleated-Front_Blouse/img_00000035.jpg', 'floral', 'train'), ('Sheer_Pleated-Front_Blouse/img_00000040.jpg', 'camo', 'train'), ('Sheer_Pleated-Front_Blouse/img_00000054.jpg', 'striped', 'test')]
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/sophisticated/Sheer_Pleated-Front_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/print/Sheer_Pleated-Front_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/floral/Sheer_Pleated-Front_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/camo/Sheer_Pleated-Front_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/striped/Sheer_Pleated-Front_Blouse
/Users/manishashivshette/Docume

/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/chevron/Side-Slit_Striped_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/dot/Side-Slit_Striped_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/patterned/Side-Slit_Striped_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/mixed/Side-Slit_Striped_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/floral/Side-Slit_Striped_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/stripe/Side-Slit_Striped_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/stripes/Side-Slit_Striped_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/leopard/Single-Button_Blazer
/Users/manishashivshette/Docu

/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/colorblocked/Boxy_Split-Neck_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/print/Southwestern_Print_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/southwestern/Southwestern_Print_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/striped/Southwestern_Print_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/print/Southwestern_Print_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/southwestern/Southwestern_Print_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/butterfly/Southwestern_Print_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/daisy/Southwestern_Print_Blouse
/U

/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/striped/Split-Back_Pleated_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/val/leopard/Split-Back_Pleated_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/camo/Split-Back_Pleated_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/striped/Split-Back_Pleated_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/heart/Split-Back_Pleated_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/print/Split-Back_Pleated_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/val/linen/Split-Back_Pleated_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/diamond/Split-Back_Pleated_Blouse
/Users/manishashivshette

/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/animal/Stripe_Print_Surplice_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/leopard/Stripe_Print_Surplice_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/val/graphic/Stripe_Print_Surplice_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/val/printed/Stripe_Print_Surplice_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/brushstroke/Stripe_Print_Surplice_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/striped/Striped_Chiffon_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/stripes/Striped_Chiffon_Blouse
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/stripe/Striped_Chiffon_Blouse
/User

...

/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/striped/Colorblocked_Lacy_Cami_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/val/striped/Colorblocked_Lacy_Cami_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/pattern/Colorblocked_Lacy_Cami_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/printed/Colorblocked_Lacy_Cami_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/stripe/Colorblocked_Lacy_Cami_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/val/colorblock/Colorblocked_Lacy_Cami_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/houndstooth/Colorblocked_Lacy_Cami_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/floral/Colorblocked

/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/print/Crepe_Woven_A-line_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/floral/Crepe_Woven_Cami_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/val/stripe/Crepe_Woven_Cami_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/floral/Crepe_Woven_Cami_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/dot/Crepe_Woven_Cami_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/heart/Crepe_Woven_Cami_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/daisy/Crepe_Woven_Cami_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/abstract/Crepe_Woven_Cami_Dress
/Users/manishashivshette/Documents/ManishaStud

/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/floral/Crocheted_Racerback_Romper
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/dots/Crocheted_Racerback_Romper
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/print/Crocheted_Shift_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/pattern/Crocheted_Shift_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/floral/Crocheted_Shift_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/sophisticated/Crocheted_Shift_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/floral/Crocheted_Shift_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/flower/Crocheted_Shift_Dress
/Users/manishashivshette/Documents/

/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/chevron/Cutout_Back_Textured_Romper
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/floral/Cutout_Back_Textured_Romper
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/val/print/Cutout_Back_Textured_Romper
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/watercolor/Cutout_Back_Textured_Romper
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/kaleidoscope/Cutout_Back_Textured_Romper
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/stripes/Cutout_Back_Textured_Romper
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/print/Cutout_Back_Textured_Romper
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/butterfly/Cutout_Back_Textu

/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/val/print/Paisley_Floral_A-Line_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/val/patterned/Paisley_Floral_A-Line_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/pattern/Paisley_Floral_A-Line_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/paisley/Paisley_High-Slit_Maxi_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/print/Paisley_High-Slit_Maxi_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/train/printed/Paisley_High-Slit_Maxi_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/paisley/Paisley_High-Slit_Maxi_Dress
/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/img/test/print/Paisley_High-Slit_Maxi_Dre

In [21]:
# move train, test and val folders to target attr model folder

shutil.move(base_path+"/train", target_attribute_model_folder+"data/") 

'/Users/manishashivshette/Documents/ManishaStudies/CMPE295B/AttributeModel/data/train'

In [22]:
shutil.move(base_path+"/test", target_attribute_model_folder+"data/") 
shutil.move(base_path+"/val", target_attribute_model_folder+"data/") 

'/Users/manishashivshette/Documents/ManishaStudies/CMPE295B/AttributeModel/data/val'

In [23]:
# get the bounding boxes for each image, preprocessing function is in other file, use these files directly now-- Manisha
train_df = pd.read_csv("dict_train.csv")
dict_train = train_df.to_dict()
test_df = pd.read_csv("dict_test.csv")
dict_test = test_df.to_dict()
val_df = pd.read_csv("dict_val.csv")
dict_val = val_df.to_dict()

In [24]:
from tensorflow.keras import Model
from tensorflow.keras.layers import Dense
from tensorflow.keras.regularizers import l2
from tensorflow.keras.optimizers import SGD
from tensorflow.keras.applications.resnet50 import ResNet50
from tensorflow.keras.preprocessing import image
from tensorflow.keras.preprocessing.image import DirectoryIterator, ImageDataGenerator
from tensorflow.keras.callbacks import ReduceLROnPlateau, ModelCheckpoint, EarlyStopping, TensorBoard
from tensorflow.keras import backend as K

In [25]:
model_resnet = ResNet50(weights='imagenet', include_top=False, pooling='avg')

In [26]:
for layer in model_resnet.layers[:-12]:
    # 6 - 12 - 18 have been tried. 12 is the best.
    layer.trainable = False

In [27]:
num_classes = len(os.listdir(target_attribute_model_folder+"data/train"))
print("Attribute classes:",num_classes)

Attribute classes: 81


In [28]:
x = model_resnet.output
x = Dense(512, activation='elu', kernel_regularizer=l2(0.001))(x)
# last layer to classify the image into one of the attribute
y = Dense(num_classes, activation='softmax', name='img')(x)

In [29]:
x_bbox = model_resnet.output
x_bbox = Dense(512, activation='relu', kernel_regularizer=l2(0.001))(x_bbox)
x_bbox = Dense(128, activation='relu', kernel_regularizer=l2(0.001))(x_bbox)
bbox = Dense(4, kernel_initializer='normal', name='bbox')(x_bbox)

In [30]:
final_model = Model(inputs=model_resnet.input,
                    outputs=[y, bbox])

In [31]:
print(final_model.summary())

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, None, None, 3 0                                            
__________________________________________________________________________________________________
conv1_pad (ZeroPadding2D)       (None, None, None, 3 0           input_1[0][0]                    
__________________________________________________________________________________________________
conv1 (Conv2D)                  (None, None, None, 6 9472        conv1_pad[0][0]                  
__________________________________________________________________________________________________
bn_conv1 (BatchNormalization)   (None, None, None, 6 256         conv1[0][0]                      
__________________________________________________________________________________________________
activation

In [32]:
class DirectoryIteratorWithBoundingBoxes(DirectoryIterator):
    def __init__(self, directory, image_data_generator, bounding_boxes: dict = None, target_size=(256, 256),
                 color_mode: str = 'rgb', classes=None, class_mode: str = 'categorical', batch_size: int = 32,
                 shuffle: bool = True, seed=None, data_format=None, save_to_dir=None,
                 save_prefix: str = '', save_format: str = 'jpeg', follow_links: bool = False):
        super().__init__(directory, image_data_generator, target_size, color_mode, classes, class_mode, batch_size,
                         shuffle, seed, data_format, save_to_dir, save_prefix, save_format, follow_links)
        self.bounding_boxes = bounding_boxes

    def next(self):
        """
        # Returns
            The next batch.
        """
        with self.lock:
            index_array = next(self.index_generator)
        # The transformation of images is not under thread lock
        # so it can be done in parallel
        batch_x = np.zeros((len(index_array),) + self.image_shape, dtype=K.floatx())
        locations = np.zeros((len(batch_x),) + (4,), dtype=K.floatx())

        grayscale = self.color_mode == 'grayscale'
        # build batch of image data
        for i, j in enumerate(index_array):
            fname = self.filenames[j]
            img = image.load_img(os.path.join(self.directory, fname),
                                 grayscale=grayscale,
                                 target_size=self.target_size)
            x = image.img_to_array(img, data_format=self.data_format)
            x = self.image_data_generator.random_transform(x)
            x = self.image_data_generator.standardize(x)
            batch_x[i] = x

            if self.bounding_boxes is not None and fname in self.bounding_boxes :
                bounding_box = self.bounding_boxes[fname]
                locations[i] = np.asarray(
                    [bounding_box['x1'], bounding_box['y1'], bounding_box['x2'], bounding_box['y2']],
                    dtype=K.floatx())
        # optionally save augmented images to disk for debugging purposes
        # build batch of labels
        if self.class_mode == 'sparse':
            batch_y = self.classes[index_array]
        elif self.class_mode == 'binary':
            batch_y = self.classes[index_array].astype(K.floatx())
        elif self.class_mode == 'categorical':
            batch_y = np.zeros((len(batch_x), num_classes), dtype=K.floatx())
            for i, label in enumerate(self.classes[index_array]):
                batch_y[i, label] = 1.
        else:
            return batch_x

        if self.bounding_boxes is not None:
            return batch_x, [batch_y, locations]
        else:
            return batch_x, batch_y

In [33]:
opt = SGD(lr=0.0001, momentum=0.9, nesterov=True)

In [34]:
final_model.compile(optimizer=opt,
                    loss={'img': 'categorical_crossentropy',
                          'bbox': 'mean_squared_error'},
                    metrics={'img': ['accuracy', 'top_k_categorical_accuracy'], # default: top-5
                             'bbox': ['mse']})

In [35]:
train_datagen = ImageDataGenerator(rotation_range=30.,
                                   shear_range=0.2,
                                   zoom_range=0.2,
                                   width_shift_range=0.2,
                                   height_shift_range=0.2,
                                   horizontal_flip=True)
test_datagen = ImageDataGenerator()

In [36]:
train_data_path = target_attribute_model_folder + "data/train/"
train_iterator = DirectoryIteratorWithBoundingBoxes(train_data_path, train_datagen, bounding_boxes=dict_train, target_size=(200, 200))
val_data_path = target_attribute_model_folder + "data/val/"
val_iterator = DirectoryIteratorWithBoundingBoxes(val_data_path, test_datagen, bounding_boxes=dict_val,target_size=(200, 200))

Found 114989 images belonging to 81 classes.
Found 19513 images belonging to 81 classes.


In [37]:
lr_reducer = ReduceLROnPlateau(monitor='val_loss',
                               patience=12,
                               factor=0.5,
                               verbose=1)
tensorboard = TensorBoard(log_dir='./logs')
early_stopper = EarlyStopping(monitor='val_loss',
                              patience=30,
                              verbose=1)


checkpoint = ModelCheckpoint(saved_model_path)

In [38]:
def custom_generator(iterator):
    while True:
        batch_x, batch_y = iterator.next()
        yield (batch_x, batch_y)

In [39]:
history = final_model.fit_generator(custom_generator(train_iterator),
                          steps_per_epoch=num_steps,
                          epochs=num_epochs, validation_data=custom_generator(val_iterator),
                          validation_steps=1000,
                          verbose=1,
                          shuffle=True,
                          callbacks=[lr_reducer, checkpoint, early_stopper, tensorboard],
                          workers=12)

Epoch 1/100
14/15 [===========================>..] - ETA: 4s - loss: 6.4850 - img_loss: 4.5802 - bbox_loss: 0.0599 - img_acc: 0.0268 - img_top_k_categorical_accuracy: 0.0893 - bbox_mean_squared_error: 0.0599

OSError: Unable to create file (unable to open file: name = '/Users/manishashivshette/Documents/ManishaStudies/CMPE295A/deep-fashion-dataset/models/model-texture.h5', errno = 2, error message = 'No such file or directory', flags = 13, o_flags = 602)

In [ ]:
import matplotlib.pyplot as plt
print(history.history.keys())
# summarize history for accuracy
plt.plot(history.history['acc'])
plt.plot(history.history['val_acc'])
plt.title('model accuracy')
plt.ylabel('accuracy')
plt.xlabel('epoch')
plt.legend(['train', 'test'], loc='upper left')
plt.show()

# summarize history for loss
plt.plot(history.history['loss'])
plt.plot(history.history['val_loss'])
plt.title('model loss')
plt.ylabel('loss')
plt.xlabel('epoch')
plt.legend(['train', 'test'], loc='upper left')
plt.show()

In [ ]:
test_datagen = ImageDataGenerator()
test_data_path = target_attribute_model_folder + "data/test/"
test_iterator = DirectoryIteratorWithBoundingBoxes(test_data_path, test_datagen, bounding_boxes=dict_test, target_size=(200, 200))
scores = final_model.evaluate_generator(custom_generator(test_iterator), steps=10)

print('Multi target loss: ' + str(scores[0]))
print('Image loss: ' + str(scores[1]))
print('Bounding boxes loss: ' + str(scores[2]))
print('Image accuracy: ' + str(scores[3]))
print('Top-5 image accuracy: ' + str(scores[4]))
print('Bounding boxes error: ' + str(scores[5]))